In [17]:
import pickle
import numpy as np
import pandas as pd
import math
from sklearn import metrics
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler, normalize
from scipy.spatial.distance import cdist
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
import warnings
warnings.filterwarnings('ignore')

In [5]:
df = pd.read_csv("C:\\Users\\dell\\Desktop\\Week1_challenge_data_source.csv")

In [6]:
user_experience_df = df[[
    'MSISDN/Number',
    'Avg RTT DL (ms)',
    'Avg RTT UL (ms)',
    'Avg Bearer TP DL (kbps)',
    'Avg Bearer TP UL (kbps)',
    'TCP DL Retrans. Vol (Bytes)',
    'TCP UL Retrans. Vol (Bytes)',
    'Handset Type']]

In [7]:
# caluclate the totals
user_experience_df['Total Avg RTT (ms)'] = user_experience_df['Avg RTT DL (ms)'] + user_experience_df['Avg RTT UL (ms)']
user_experience_df['Total Avg Bearer TP (kbps)'] = user_experience_df['Avg Bearer TP DL (kbps)'] + user_experience_df['Avg Bearer TP UL (kbps)']
user_experience_df['Total TCP Retrans. Vol (Bytes)'] = user_experience_df['TCP DL Retrans. Vol (Bytes)'] + user_experience_df['TCP UL Retrans. Vol (Bytes)']
user_experience_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150001 entries, 0 to 150000
Data columns (total 11 columns):
 #   Column                          Non-Null Count   Dtype  
---  ------                          --------------   -----  
 0   MSISDN/Number                   148935 non-null  float64
 1   Avg RTT DL (ms)                 122172 non-null  float64
 2   Avg RTT UL (ms)                 122189 non-null  float64
 3   Avg Bearer TP DL (kbps)         150000 non-null  float64
 4   Avg Bearer TP UL (kbps)         150000 non-null  float64
 5   TCP DL Retrans. Vol (Bytes)     61855 non-null   float64
 6   TCP UL Retrans. Vol (Bytes)     53352 non-null   float64
 7   Handset Type                    149429 non-null  object 
 8   Total Avg RTT (ms)              122161 non-null  float64
 9   Total Avg Bearer TP (kbps)      150000 non-null  float64
 10  Total TCP Retrans. Vol (Bytes)  50471 non-null   float64
dtypes: float64(10), object(1)
memory usage: 12.6+ MB


In [10]:
user_experience_df = user_experience_df[['MSISDN/Number', 'Handset Type', 'Total Avg RTT (ms)',
    'Total Avg Bearer TP (kbps)', 'Total TCP Retrans. Vol (Bytes)']]

In [11]:
# aggregating user experience metrics per user
user_experience_df1 = user_experience_df.groupby(
    'MSISDN/Number').agg({
        'Total Avg RTT (ms)': 'sum',
        'Total Avg Bearer TP (kbps)': 'sum',
        'Total TCP Retrans. Vol (Bytes)': 'sum',
        'Handset Type': [lambda x: x.mode()[0]]})
user_experience_df1.head()

Total Avg RTT (ms) Total Avg Bearer TP (kbps)  \
                             sum                        sum   
MSISDN/Number                                                 
3.360100e+10                46.0                       76.0   
3.360100e+10                31.0                       99.0   
3.360100e+10                 0.0                       97.0   
3.360101e+10                84.0                      248.0   
3.360101e+10               119.0                    56844.0   

              Total TCP Retrans. Vol (Bytes)                    Handset Type  
                                         sum                        <lambda>  
MSISDN/Number                                                                 
3.360100e+10                             0.0  Huawei P20 Lite Huawei Nova 3E  
3.360100e+10                             0.0          Apple iPhone 7 (A1778)  
3.360100e+10                             0.0                       undefined  
3.360101e+10                             0.0         Apple iPhone 5S (A1457)  
3.360101e+10                       9370832.0         Apple iPhone Se (A1723)

In [12]:
user_experience_df = pd.DataFrame(columns=[
    "Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)",
    "Handset Type"])

user_experience_df["Total Avg RTT (ms)"] = user_experience_df1["Total Avg RTT (ms)"]['sum']
user_experience_df["Total Avg Bearer TP (kbps)"] = user_experience_df1["Total Avg Bearer TP (kbps)"]['sum']
user_experience_df["Total TCP Retrans. Vol (Bytes)"] = user_experience_df1["Total TCP Retrans. Vol (Bytes)"]['sum']
user_experience_df["Handset Type"] = user_experience_df1["Handset Type"]['<lambda>']
user_experience_df.head()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  \
MSISDN/Number                                                   
3.360100e+10                 46.0                        76.0   
3.360100e+10                 31.0                        99.0   
3.360100e+10                  0.0                        97.0   
3.360101e+10                 84.0                       248.0   
3.360101e+10                119.0                     56844.0   

               Total TCP Retrans. Vol (Bytes)                    Handset Type  
MSISDN/Number                                                                  
3.360100e+10                              0.0  Huawei P20 Lite Huawei Nova 3E  
3.360100e+10                              0.0          Apple iPhone 7 (A1778)  
3.360100e+10                              0.0                       undefined  
3.360101e+10                              0.0         Apple iPhone 5S (A1457)  
3.360101e+10                        9370832.0         Apple iPhone Se (A1723)

## Top 10 values of the experience metrics

In [13]:
# top 10 rtt values in the dataset

rtt = user_experience_df.sort_values('Total Avg RTT (ms)', ascending=False)
top_10 = rtt.head(10)['Total Avg RTT (ms)']
bottom_10 = rtt.tail(10)['Total Avg RTT (ms)']
most_10 = user_experience_df['Total Avg RTT (ms)'].value_counts().head(10)

In [19]:
def plotly_multi_hist(sr, rows, cols, title_text, subplot_titles):
  fig = make_subplots(rows=rows, cols=cols, subplot_titles=subplot_titles)
  for i in range(rows):
    for j in range(cols):
      x = ["-> " + str(i) for i in sr[i+j].index]
      fig.add_trace(go.Bar(x=x, y=sr[i+j].values ), row=i+1, col=j+1)
  fig.update_layout(showlegend=False, title_text=title_text)
  fig.show()

In [47]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3, "RTT values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

In [21]:
# top 10 tp values in the dataset

tp = user_experience_df.sort_values('Total Avg Bearer TP (kbps)', ascending=False)
top_10 = tp.head(10)['Total Avg Bearer TP (kbps)']
bottom_10 = tp.tail(10)['Total Avg Bearer TP (kbps)']
most_10 = user_experience_df['Total Avg Bearer TP (kbps)'].value_counts().head(10)

In [46]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3,
    "TP values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

In [23]:
# top 10 tcp values in the dataset

tcp = user_experience_df.sort_values('Total TCP Retrans. Vol (Bytes)', ascending=False)
top_10 = tcp.head(10)['Total TCP Retrans. Vol (Bytes)']
bottom_10 = tcp.tail(10)['Total TCP Retrans. Vol (Bytes)']
most_10 = user_experience_df['Total TCP Retrans. Vol (Bytes)'].value_counts().head(10)

In [24]:
plotly_multi_hist([top_10, bottom_10, most_10], 1, 3,
    "TCP values in the dataset", ['Top 10', 'Bottom 10', 'Most 10'])

# Average values of experience metrics per handset type

In [25]:
handset_type_df = user_experience_df.groupby('Handset Type').mean()
handset_type_df.head()

Total Avg RTT (ms)  \
Handset Type                                            
A-Link Telecom I. Cubot A5                       42.0   
A-Link Telecom I. Cubot Note Plus              1589.0   
A-Link Telecom I. Cubot Note S                  890.0   
A-Link Telecom I. Cubot Nova                     44.0   
A-Link Telecom I. Cubot Power                    43.0   

                                   Total Avg Bearer TP (kbps)  \
Handset Type                                                    
A-Link Telecom I. Cubot A5                            23510.0   
A-Link Telecom I. Cubot Note Plus                      6699.0   
A-Link Telecom I. Cubot Note S                         8937.0   
A-Link Telecom I. Cubot Nova                          56217.0   
A-Link Telecom I. Cubot Power                         69468.0   

                                   Total TCP Retrans. Vol (Bytes)  
Handset Type                                                       
A-Link Telecom I. Cubot A5                                    0.0  
A-Link Telecom I. Cubot Note Plus                        616213.0  
A-Link Telecom I. Cubot Note S                         41411731.0  
A-Link Telecom I. Cubot Nova                             137170.0  
A-Link Telecom I. Cubot Power                              8041.0

In [26]:
# sorting per tp
tp = handset_type_df.sort_values(
    'Total Avg Bearer TP (kbps)', ascending=False)
tp.head()

Total Avg RTT (ms)  \
Handset Type                                             
Spa Condor Elect. Allure M2                       90.0   
Huawei Par-Lx9                                   259.0   
Huawei B715S-23C                                 153.6   
Asustek Wireless-Ac1200 Lte Router               207.0   
New-Bund Technol. Thor                            81.5   

                                    Total Avg Bearer TP (kbps)  \
Handset Type                                                     
Spa Condor Elect. Allure M2                           168623.0   
Huawei Par-Lx9                                        144115.0   
Huawei B715S-23C                                      141692.5   
Asustek Wireless-Ac1200 Lte Router                    125525.0   
New-Bund Technol. Thor                                113444.5   

                                    Total TCP Retrans. Vol (Bytes)  
Handset Type                                                        
Spa Condor Elect. Allure M2                                89016.0  
Huawei Par-Lx9                                           2896635.0  
Huawei B715S-23C                                        42876845.8  
Asustek Wireless-Ac1200 Lte Router                       8773966.0  
New-Bund Technol. Thor                                   3914693.0

In [27]:
# sorting per tcp
tcp = handset_type_df.sort_values(
    'Total TCP Retrans. Vol (Bytes)', ascending=False)
tcp.head()

Total Avg RTT (ms)  \
Handset Type                                              
Huawei Bln-Al10                                  292.00   
Asustek Asus Zenfone Selfie Zd551Kl              121.50   
Samsung Galaxy Tab S3 (Sm-T825)                  121.50   
Huawei E5776S-32                                 169.75   
Apple iPad Pro (A1652)                            28.50   

                                     Total Avg Bearer TP (kbps)  \
Handset Type                                                      
Huawei Bln-Al10                                     5761.000000   
Asustek Asus Zenfone Selfie Zd551Kl                27585.000000   
Samsung Galaxy Tab S3 (Sm-T825)                    34720.000000   
Huawei E5776S-32                                   31572.500000   
Apple iPad Pro (A1652)                             26039.833333   

                                     Total TCP Retrans. Vol (Bytes)  
Handset Type                                                         
Huawei Bln-Al10                                        3.291746e+08  
Asustek Asus Zenfone Selfie Zd551Kl                    3.216583e+08  
Samsung Galaxy Tab S3 (Sm-T825)                        2.532841e+08  
Huawei E5776S-32                                       2.056437e+08  
Apple iPad Pro (A1652)                                 1.169219e+08

# K-means Clustering


In [30]:
user_experience_df = user_experience_df[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]]

In [31]:
# scale data
scaler = StandardScaler()
scaled_data = scaler.fit_transform(user_experience_df)
scaled_data

array([[-0.14425818, -0.49274715, -0.0796073 ],
       [-0.16671505, -0.49220516, -0.0796073 ],
       [-0.21312591, -0.49225229, -0.0796073 ],
       ...,
       [-0.21312591, -0.49451452, -0.0796073 ],
       [-0.21312591, -0.49376044, -0.0796073 ],
       [-0.21312591, -0.49449095, -0.0796073 ]])

In [32]:
normalized_data = normalize(scaled_data)
normalized_data

array([[-0.27765199, -0.94838455, -0.15321921],
       [-0.3171086 , -0.93622317, -0.151421  ],
       [-0.39301507, -0.90773837, -0.14679992],
       ...,
       [-0.39153183, -0.90846847, -0.1462459 ],
       [-0.39202513, -0.90822602, -0.14643016],
       [-0.39154722, -0.90846091, -0.14625165]])

In [33]:
kmeans = KMeans(n_clusters=3, random_state=1).fit(normalized_data)
kmeans.labels_

array([0, 0, 0, ..., 0, 0, 0])

In [34]:
user_experience_df.insert(0, 'cluster', kmeans.labels_)
user_experience_df

cluster  Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  \
MSISDN/Number                                                            
3.360100e+10         0                46.0                        76.0   
3.360100e+10         0                31.0                        99.0   
3.360100e+10         0                 0.0                        97.0   
3.360101e+10         0                84.0                       248.0   
3.360101e+10         1               119.0                     56844.0   
...                ...                 ...                         ...   
3.379000e+10         0                52.0                     10365.0   
3.379000e+10         0                40.0                       116.0   
3.197021e+12         0                 0.0                         1.0   
3.370000e+14         0                 0.0                        33.0   
8.823971e+14         0                 0.0                         2.0   

               Total TCP Retrans. Vol (Bytes)  
MSISDN/Number                                  
3.360100e+10                              0.0  
3.360100e+10                              0.0  
3.360100e+10                              0.0  
3.360101e+10                              0.0  
3.360101e+10                        9370832.0  
...                                       ...  
3.379000e+10                         218045.0  
3.379000e+10                              0.0  
3.197021e+12                              0.0  
3.370000e+14                              0.0  
8.823971e+14                              0.0  

[106856 rows x 4 columns]

In [35]:
user_experience_df['cluster'].value_counts()

0    70708
1    28716
2     7432
Name: cluster, dtype: int64

In [38]:
fig = px.scatter(user_experience_df, x='Total TCP Retrans. Vol (Bytes)', y='Total Avg Bearer TP (kbps)',
                 color='cluster', size='Total Avg RTT (ms)')
fig.update_traces(marker_size=8)
fig.update(layout_yaxis_range = [0, 400000])
fig.update(layout_xaxis_range = [0, 4000000000])
fig.show()

In [39]:
cluster0 = user_experience_df[user_experience_df["cluster"]==0]
cluster0[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  \
count        70708.000000                70708.000000   
mean            46.889560                 1919.374371   
std             47.280992                 4493.534075   
min              0.000000                    0.000000   
25%              0.000000                   86.000000   
50%             39.000000                  112.000000   
75%             63.000000                  385.000000   
max            274.000000                21669.000000   

       Total TCP Retrans. Vol (Bytes)  
count                    7.070800e+04  
mean                     4.520877e+05  
std                      5.684353e+06  
min                      0.000000e+00  
25%                      0.000000e+00  
50%                      0.000000e+00  
75%                      0.000000e+00  
max                      2.699893e+08

In [40]:
cluster1 = user_experience_df[user_experience_df["cluster"]==1]
cluster1[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  \
count        28716.000000                28716.000000   
mean           156.445953                70721.547604   
std            186.740619                56679.588576   
min              0.000000                20462.000000   
25%             63.000000                35689.000000   
50%             98.000000                53070.000000   
75%            168.000000                83617.750000   
max           5847.000000               902222.000000   

       Total TCP Retrans. Vol (Bytes)  
count                    2.871600e+04  
mean                     4.032178e+07  
std                      2.826391e+08  
min                      0.000000e+00  
25%                      1.020742e+05  
50%                      1.285374e+06  
75%                      7.105919e+06  
max                      8.354209e+09

In [41]:
cluster2 = user_experience_df[user_experience_df["cluster"]==2]
cluster2[["Total Avg RTT (ms)",
    "Total Avg Bearer TP (kbps)",
    "Total TCP Retrans. Vol (Bytes)"]].describe()

Total Avg RTT (ms)  Total Avg Bearer TP (kbps)  \
count         7432.000000                 7432.000000   
mean           996.193757                10219.717304   
std           2333.008379                12455.234272   
min             39.000000                    0.000000   
25%            296.000000                  660.750000   
50%            444.000000                 6344.000000   
75%            945.000000                16489.250000   
max          96924.000000               209835.000000   

       Total TCP Retrans. Vol (Bytes)  
count                    7.432000e+03  
mean                     1.316963e+07  
std                      1.271165e+08  
min                      0.000000e+00  
25%                      1.507500e+02  
50%                      3.325590e+05  
75%                      2.851766e+06  
max                      4.301477e+09

In [43]:
# save the dataframe
user_experience_df.to_csv("C://Users//dell//Desktop//user_experience_data.csv")

In [44]:
with open("C://Users//dell//Desktop//user_exp.pkl", "wb") as f:
    pickle.dump(kmeans, f)